In [ ]:
from re import S
import numpy as np
import json
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from numpy import core
import torch
import tqdm
from sklearn.metrics import ndcg_score
import pickle



In [ ]:
sentires = '/content/drive/MyDrive/beauty.txt'
reviewData='/content/drive/MyDrive/Beauty_5.json'
sentires

'/content/drive/MyDrive/beauty.txt'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
lr = 0.01
f_threshold = 5
u_threshold =10
test_length = 5
val_length = 1
sample_ratio =2
neg_length = 100
lam = 200
alp = 0.05
gam = 1
test_num = 1
rec_k = 5
step = 1000
mask_thresh = 0.1
user_mask =False
threshold = 0.1
range_i =0
range_j =5
Alpha = 0.05
Lambda = 200
gamma = 1




IndentationError: ignored

In [ ]:
def get_u_i_and_i_u_dict(data):
    user_item_dict = {}
    item_user_dict = {}
    feature_count_dict = {}
    for row in data:
        user = row[0]
        item = row[1]
        if user not in user_item_dict:
            user_item_dict[user] = [item]
        else:
            user_item_dict[user].append(item)
        if item not in item_user_dict:
            item_user_dict[item] = [user]
        else:
            item_user_dict[item].append(user)
        for feature in row[2:]:
            feature_name = feature[0]
            if feature_name not in feature_count_dict:
                  feature_count_dict[feature_name] = 1
            else:
                  feature_count_dict[feature_name] += 1
    feature_list = [feature_name for feature_name, count in feature_count_dict.items() if count >= f_threshold ]

    return user_item_dict, item_user_dict,feature_count_dict

In [ ]:
def get_user_attention_matrix(sentiment_data, user_num, feature_num, max_range=5):
    print(feature_num)
    user_counting_matrix = np.zeros((user_num, feature_num))  # tij = x if user i mention feature j x times
    print(len(sentiment_data))
    for row in sentiment_data:
        user = row[0]
        for fos in row[2:]:
            feature = fos[0]
            user_counting_matrix[user, feature] += 1
    print(user_counting_matrix)
    user_attention_matrix = np.zeros((user_num, feature_num))  # xij = [1-N], normalized attention matrix
    for i in range(len(user_counting_matrix)):
        for j in range(len(user_counting_matrix[i])):
            if user_counting_matrix[i, j] == 0:
                norm_v = 0  # if nor mentioned: 0
            else:
                norm_v = 1 + (max_range - 1) * ((2 / (1 + np.exp(-user_counting_matrix[i, j]))) - 1)  # norm score
            user_attention_matrix[i, j] = norm_v
    user_attention_matrix = np.array(user_attention_matrix, dtype='float32')
    return user_attention_matrix

In [ ]:
def get_item_quality_matrix(sentiment_data, item_num, feature_num, max_range=5):
    item_counting_matrix = np.zeros((item_num, feature_num))  # kij = x if item i's feature j is mentioned x times
    item_sentiment_matrix = np.zeros((item_num, feature_num))  # sij = x if the overall rating is x (sum up)
    for row in sentiment_data:
        item = row[1]
        for fos in row[2:]:
            feature = fos[0]
            sentiment = fos[2]
            item_counting_matrix[item, feature] += 1
            if sentiment == '+1':
                item_sentiment_matrix[item, feature] += 1
            elif sentiment == '-1':
                item_sentiment_matrix[item, feature] -= 1
            else:
                print("sentiment data error: the sentiment value can only be +1 or -1")
                exit(1)
    item_quality_matrix = np.zeros((item_num, feature_num))
    for i in range(len(item_counting_matrix)):
        for j in range(len(item_counting_matrix[i])):
            if item_counting_matrix[i, j] == 0:
                norm_v = 0  # if not mentioned: 0
            else:
                norm_v = 1 + ((max_range - 1) / (1 + np.exp(-item_sentiment_matrix[i, j])))  # norm score
            item_quality_matrix[i, j] = norm_v
    item_quality_matrix = np.array(item_quality_matrix, dtype='float32')
    return item_quality_matrix

In [ ]:
def sample_training_pairs(user, training_items, item_set, sample_ratio=10):
    positive_items = set(training_items)
    negative_items = set()
    for item in item_set:
        if item not in positive_items:
            negative_items.add(item)
    neg_length = len(positive_items) * sample_ratio
    negative_items = np.random.choice(np.array(list(negative_items)), neg_length, replace=False)
    train_pairs = []
    for p_item in positive_items:
        train_pairs.append([user, p_item, 1])
    for n_item in negative_items:
        train_pairs.append([user, n_item, 0])
    # print(train_pairs)
    return train_pairs

In [ ]:
class DataExtractor:
    def __init__(self, sentires, train_ratio=0.8):
        self.sentiment_data = []
        self.user_dict = {}
        self.item_dict = {}
        self.feature_dict = {}
        # self.user_item_dict = {}
        # self.item_user_dict = {}
        self.user_list = []
        self.item_list = []
        self.feature_list = []
        self.num_users = 0
        self.num_items = 0
        self.num_features = 0
        self.user_hist_inter_dict = {}
        self.item_hist_inter_dict = {}
        self.user_feature_matrix = None
        self.item_feature_matrix = None
        self.train_data = []
        self.test_data = []
        self.preprocessSentimentData()
        # self.filter_feature()
        self.sample_training()
        self.sample_test()
    def get_user_dict(self,):
        self.user_dict = {}
        for row in self.sentiment_data:
            user_id = row[0]
            if user_id not in self.user_dict:
                self.user_dict[user_id] = len(self.user_dict)
        # return user_dict

    def get_item_dict(self,):
        self.item_dict = {}
        for row in self.sentiment_data:
            item_id = row[1]
            if item_id not in self.item_dict:
                self.item_dict[item_id] = len(self.item_dict)
        # return item_dict

    def get_feature_dict(self):
      self.feature_dict = {}
      for row in self.sentiment_data:
          if len(row) > 2:
              for feature in row[2:]:
                  feature_name = feature[0]
                  if feature_name not in self.feature_dict:
                      self.feature_dict[feature_name] = len(self.feature_dict)
      # return feature_dict
    def preprocessSentimentData(self):
      with open(sentires,'r') as f:
        line = f.readline().strip()
        while line:
            user = line.split('@')[0]
            item = line.split('@')[1]
            self.sentiment_data.append([user, item])
            l = len(user) + len(item)
            fosr_data = line[l+3:]
            for seg in fosr_data.split('||'):
              fos = seg.split(':')[0].strip('|')
              if len(fos.split('|')) > 1:
                feature = fos.split('|')[0]
                opinion = fos.split('|')[1]
                sentiment = fos.split('|')[2]
                self.sentiment_data[-1].append([feature, opinion, sentiment])
            line = f.readline().strip()
        self.sentiment_data = np.array(self.sentiment_data)
        self.sentiment_review()
        self.get_user_item_feature_matrix()

    def filter_feature(self):
      print("Len",len(self.sentiment_data))
      #Count of everything
      user_item_dict,item_user_dict, feature_count_dict = get_u_i_and_i_u_dict(self.sentiment_data)
      print("Extracted data stats : ")
      print("Users : ",len(user_item_dict))
      print("Items : ",len(item_user_dict))
      print("Feature : ",len(feature_count_dict))
      f_set= set()
      for k,v in feature_count_dict.items():
        if v>f_threshold:
          f_set.add(k)
      filter_data =[]
      for r in self.sentiment_data:
        filter_data.append([r[0],r[1]])
        for fos in r[2:]:
          if fos[0] in f_set:
            filter_data[-1].append(fos)
        if len(filter_data[-1])==2:
          del filter_data[-1]
      self.sentiment_data =np.array(filter_data)
      print("Len",len(self.sentiment_data))
      user_item_dict,item_user_dict, feature_count_dict = get_u_i_and_i_u_dict(self.sentiment_data)
      print("Extracted data stats : ")
      print("Users : ",len(user_item_dict))
      print("Items : ",len(item_user_dict))
      print("Feature : ",len(feature_count_dict))
      filter_data =[]
      u_set= set()
      for k,v in user_item_dict.items():
        if len(v)>=u_threshold:
          u_set.add(k)
      for r in self.sentiment_data:
         if r[0] in u_set:
            filter_data.append([r[0],r[1]])
            for fos in r[2:]:
                filter_data[-1].append(fos)
      self.sentiment_data = np.array(filter_data)
      print("Len",len(self.sentiment_data))
      user_item_dict,item_user_dict, feature_count_dict = get_u_i_and_i_u_dict(self.sentiment_data)
      print("Extracted data stats : ")
      print("Users : ",len(user_item_dict))
      print("Items : ",len(item_user_dict))
      print("Feature : ",len(feature_count_dict))




    def sentiment_review(self):
      # self.get_user_dict()
      # self.get_item_dict()
      # self.get_feature_dict()
      # print("----Initial Raw Data---")
      # print("Users : ",len(self.user_dict))
      # print("Items : ",len(self.item_dict))
      # print("Features : ",len(self.feature_dict))

      self.filter_feature()
      self.filter_feature()
      print("After 2 filters:",len(self.sentiment_data))
      user_item_dict,item_user_dict, feature_count_dict = get_u_i_and_i_u_dict(self.sentiment_data)
      print("Extracted data stats in sentreview: ")
      print("After 2 filters:",len(self.sentiment_data))
      print("Users : ",len(user_item_dict))
      print("Items : ",len(item_user_dict))
      print("Feature : ",len(feature_count_dict))
      user_item_date_dict ={}
      for i, line in enumerate(open(reviewData, "r")):
          record = json.loads(line)
          user = record['reviewerID']
          item = record['asin']
          date = record['unixReviewTime']
          if user in user_item_dict and item in user_item_dict[user] and (user, item) not in user_item_date_dict:
              # print(i)
              user_item_date_dict[(user, item)] = date
      print("I is",i)
      print("UID len",len(user_item_date_dict))
      self.sentiment_data = [row for row in self.sentiment_data if (row[0], row[1]) in user_item_date_dict]

      self.filter_feature()

      user_item_dict,item_user_dict, feature_count_dict = get_u_i_and_i_u_dict(self.sentiment_data)
      print("Extracted data stats after item date filter : ")
      print("Users : ",len(user_item_dict))
      print("Items : ",len(item_user_dict))
      print("Feature : ",len(feature_count_dict))
      for key in list(user_item_date_dict.keys()):
            if key[0] not in user_item_dict or key[1] not in user_item_dict[key[0]]:
                del user_item_date_dict[key]
      print("UID len",len(user_item_date_dict))
      # self.get_user_dict()
      # self.get_item_dict()
      # self.get_feature_dict()
      user_dict={}
      item_dict={}
      f_dict={}
      f_list= []
      # feature_list = []
      for row in self.sentiment_data:
          for fos in row[2:]:
              feature = fos[0]
              if feature not in f_list:
                  f_list.append(feature)
      f_list = np.array(f_list)
      count = 0
      for user in user_item_dict:
          if user not in user_dict:
              user_dict[user] = count
              count += 1
      count = 0
      for item in item_user_dict:
           if item not in item_dict:
              item_dict[item] = count
              count += 1
      count = 0
      for feature in f_list:
          if feature not in f_dict:
              f_dict[feature] = count
              count += 1
      print("UD len",len(user_dict))
      print("ID len",len(item_dict))
      print("FD len",len(f_dict))
      for i in range(len(self.sentiment_data)):
        self.sentiment_data[i][0] = user_dict[self.sentiment_data[i][0]]
        self.sentiment_data[i][1] = item_dict[self.sentiment_data[i][1]]
        for j in range(len(self.sentiment_data[i]) - 2):
          self.sentiment_data[i][j+2][0] = f_dict[self.sentiment_data[i][j + 2][0]]

      mapped_user_item_date_dict = {}
      for key, value in user_item_date_dict.items():
          mapped_user_item_date_dict[user_dict[key[0]], item_dict[key[1]]] = value
          user_item_date_dict = mapped_user_item_date_dict
      user_item_date_dict = dict(sorted(user_item_date_dict.items(), key=lambda item: item[1]))
      print("UID len sorted",len(user_item_date_dict))
      self.user_hist_inter_dict = {}
      self.item_hist_inter_dict = {}
      for key, value in user_item_date_dict.items():
          user = key[0]
          item = key[1]
          if user not in self.user_hist_inter_dict:
              self.user_hist_inter_dict[user] = [item]
          else:
              self.user_hist_inter_dict[user].append(item)
          if item not in self.item_hist_inter_dict:
              self.item_hist_inter_dict[item] = [user]
          else:
              self.item_hist_inter_dict[item].append(user)
      self.user_hist_inter_dict = dict(sorted(self.user_hist_inter_dict.items()))
      self.item_hist_inter_dict = dict(sorted(self.item_hist_inter_dict.items()))
      # for k,v in self.user_hist_inter_dict.items():
      #     print("user_hist_inter_dict",k,len(v),v)
      # for k,v in self.item_hist_inter_dict.items():
      #     print("item_hist_inter_dict",k,len(v),v)
      self.user_list = list(self.user_hist_inter_dict.keys())
      self.item_list = list(self.item_hist_inter_dict.keys())
      self.user_dict = user_dict
      self.item_dict = item_dict
      self.feature_dict = f_dict
      print("----After final filtering Data Again---")
      user_item_dict,item_user_dict, feature_count_dict = get_u_i_and_i_u_dict(self.sentiment_data)
      # print("Extracted data stats after item date filter : ")
      print("Users : ",len(user_item_dict))
      print("Items : ",len(item_user_dict))
      print("Feature : ",len(f_list))
      self.num_users = len(self.user_dict)
      self.num_items = len(self.item_dict)
      self.num_features = len(self.feature_dict)
      self.features= f_list
      print("Users : ",self.num_users)
      print("Items : ",self.num_items)
      print("Features : ",self.num_features)


    def get_user_item_feature_matrix(self,):
        train_u_i_set = set()
        for user, items in self.user_hist_inter_dict.items():
            items = items[:-test_length]
            for item in items:
                train_u_i_set.add((user, item))
        print("train_u_I",len(train_u_i_set))
        train_sentiment_data = []
        for row in self.sentiment_data:
            user = row[0]
            item = row[1]
            if (user, item) in train_u_i_set:
                train_sentiment_data.append(row)
        print("train_sentime_set",len(train_sentiment_data))
        print(train_sentiment_data[:100])
        self.user_feature_matrix = get_user_attention_matrix(
            train_sentiment_data,
            self.num_users,
            self.num_features,
            max_range=5)
        self.item_feature_matrix = get_item_quality_matrix(
            train_sentiment_data,
            self.num_items,
            self.num_features,
            max_range=5)
        return True

    def sample_training(self):
        print('======================= sample training data =======================')
        # print(self.user_feature_matrix.shape, self.item_feature_matrix.shape)
        training_data = []
        item_set = set(self.item_list)
        for user, items in self.user_hist_inter_dict.items():
            items = items[:-(test_length+val_length)]
            training_pairs = sample_training_pairs(
                user,
                items,
                item_set,
                sample_ratio)
            for pair in training_pairs:
                training_data.append(pair)
        print('# training samples :', len(training_data))
        self.training_data = np.array(training_data)
        return True

    def sample_test(self):
        print('======================= sample test data =======================')
        user_item_label_list = []  # [[u, [item1, item2, ...], [l1, l2, ...]], ...]
        for user, items in self.user_hist_inter_dict.items():
            items = items[-(test_length+val_length):]
            user_item_label_list.append([user, items, np.ones(len(items))])  # add the test items
            negative_items = [item for item in self.item_list if
                item not in self.user_hist_inter_dict[user]]  # the not interacted items
            negative_items = np.random.choice(np.array(negative_items), neg_length, replace=False)
            user_item_label_list[-1][1] = np.concatenate((user_item_label_list[-1][1], negative_items), axis=0)
            user_item_label_list[-1][2] = np.concatenate((user_item_label_list[-1][2], np.zeros(neg_length)), axis=0)
        print('# test samples :', len(user_item_label_list))
        self.test_data = np.array(user_item_label_list)
        return True






In [ ]:
s = DataExtractor(sentires)

<ipython-input-9-88503535a3d2>:67: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  self.sentiment_data = np.array(self.sentiment_data)


Len 198502
Extracted data stats : 
Users :  22363
Items :  12101
Feature :  1988


<ipython-input-9-88503535a3d2>:91: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  self.sentiment_data =np.array(filter_data)


Len 132854
Extracted data stats : 
Users :  21983
Items :  12037
Feature :  819


<ipython-input-9-88503535a3d2>:108: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  self.sentiment_data = np.array(filter_data)


Len 49613
Extracted data stats : 
Users :  2666
Items :  9441
Feature :  808
Len 49613
Extracted data stats : 
Users :  2666
Items :  9441
Feature :  808
Len 49513
Extracted data stats : 
Users :  2666
Items :  9429
Feature :  581
Len 49450
Extracted data stats : 
Users :  2659
Items :  9423
Feature :  581
After 2 filters: 49450
Extracted data stats in sentreview: 
After 2 filters: 49450
Users :  2659
Items :  9423
Feature :  581
I is 198501
UID len 49450
Len 49450
Extracted data stats : 
Users :  2659
Items :  9423
Feature :  581
Len 49450
Extracted data stats : 
Users :  2659
Items :  9423
Feature :  581
Len 49450
Extracted data stats : 
Users :  2659
Items :  9423
Feature :  581
Extracted data stats after item date filter : 
Users :  2659
Items :  9423
Feature :  581
UID len 49450
UD len 2659
ID len 9423
FD len 581
UID len sorted 49450
----After final filtering Data Again---
Users :  2659
Items :  9423
Feature :  581
Users :  2659
Items :  9423
Features :  581
train_u_I 36155
train_

<ipython-input-9-88503535a3d2>:301: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  self.test_data = np.array(user_item_label_list)


In [ ]:
class UserItemInterDataset(Dataset):
    def __init__(self, data, user_feature_matrix, item_feature_matrix):
        self.data = np.array(data)
        self.user_feature_matrix = user_feature_matrix
        self.item_feature_matrix = item_feature_matrix

    def __getitem__(self, index):
        user = self.data[index][0]
        item = self.data[index][1]
        label = self.data[index][2]
        user_feature = self.user_feature_matrix[user]
        # print(user_feature.shape)
        item_feature = self.item_feature_matrix[item]
        # print(item_feature.shape)
        return user_feature, item_feature, label
    def __len__(self):
        return len(self.data)
Dataset = UserItemInterDataset(s.training_data,s.user_feature_matrix,s.item_feature_matrix)
train_loader = DataLoader(dataset = Dataset,batch_size=128,shuffle=True)

In [ ]:
class BaseRecModel(torch.nn.Module):
    def __init__(self, feature_length):
        super(BaseRecModel, self).__init__()
        self.fc = torch.nn.Sequential(
            torch.nn.Linear(feature_length * 2, 1024),
            torch.nn.ReLU(),
            torch.nn.Linear(1024, 256),
            torch.nn.ReLU(),
            torch.nn.Linear(256, 1),
            torch.nn.Sigmoid()
          )

    def forward(self, user_feature, item_feature):
        fusion = torch.cat((user_feature, item_feature), 1)
        out = self.fc(fusion)
        return out
model = BaseRecModel(s.num_features)
loss_fn = torch.nn.BCELoss()
optimizer = torch.optim.SGD(model.parameters(), lr=0.0005, weight_decay=1e-5)

In [ ]:
class BaseRecModel2(torch.nn.Module):
    def __init__(self, feature_length):
        super(BaseRecModel2, self).__init__()
        self.fc = torch.nn.Sequential(
            torch.nn.Linear(feature_length * 2, 1024),
            torch.nn.BatchNorm1d(1024),
            torch.nn.ReLU(),
            torch.nn.Linear(1024, 256),
            torch.nn.BatchNorm1d(256),
            torch.nn.ReLU(),
            torch.nn.Linear(256, 1),
            torch.nn.Sigmoid()
        )

    def forward(self, user_feature, item_feature):
        fusion = torch.cat((user_feature, item_feature), 1)
        out = self.fc(fusion)
        return out
model2 = BaseRecModel2(s.num_features)
loss_fn2 = torch.nn.BCELoss()
optimizer2 = torch.optim.SGD(model.parameters(), lr=0.0005, weight_decay=1e-5)

In [ ]:
def compute_ndcg(test_data, user_feature_matrix, item_feature_matrix, k, model):
    model.eval()
    ndcgs = []
    with torch.no_grad():
        for row in test_data:
            user = row[0]
            items = row[1]
            gt_labels = row[2]
            # print(gt_labels)
            user_features = np.array([user_feature_matrix[user] for i in range(len(items))])
            item_features = np.array([item_feature_matrix[item] for item in items])
            # print(user_features)
            # print(item_features)
            scores = model(torch.from_numpy(user_features),
                                      torch.from_numpy(item_features)).squeeze()
            scores = np.array(scores)
            # print("scores at ",user," are ",scores)
            # print("Labels at ",user," are ",gt_labels)
            # print("Real ndcg",ndcg_score([gt_labels],[scores],k=5))
            ndcg = ndcg_score([gt_labels], [scores], k=k)
            # print(ndcg)
            ndcgs.append(ndcg)
    print(ndcgs)
    ave_ndcg = np.mean(ndcgs)
    return ave_ndcg

In [ ]:
ndcg = compute_ndcg(s.test_data,s.user_feature_matrix,s.item_feature_matrix, 5, model)
print('init ndcg:', ndcg)
for epoch in tqdm.trange(100):
    model.train()
    optimizer.zero_grad()
    losses = []
    for user_behaviour_feature, item_aspect_feature, label in train_loader:
        user_behaviour_feature = user_behaviour_feature
        item_aspect_feature = item_aspect_feature
        label = label.float()
        out = model(user_behaviour_feature, item_aspect_feature).squeeze()
        loss = loss_fn(out, label)
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()
        losses.append(loss.detach().numpy())
        ave_train = np.mean(np.array(losses))
    print('epoch %d: ' % epoch, 'training loss: ', ave_train)
    # compute necg
    if epoch % 10 == 0:
        ndcg = compute_ndcg(s.test_data, s.user_feature_matrix, s.item_feature_matrix, 5, model)
        print('epoch %d: ' % epoch, 'training loss: ', ave_train, 'NDCG: ', ndcg)

[0.0, 0.2139862647345275, 0.0, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.3391602052736161, 0.0, 0.0, 0.16958010263680806, 0.2772734273550482, 0.0, 0.13120507751234178, 0.0, 0.0, 0.0, 0.0, 0.1460683498427064, 0.0, 0.3391602052736161, 0.0, 0.3391602052736161, 0.2772734273550482, 0.0, 0.0, 0.0, 0.3391602052736161, 0.0, 0.0, 0.38356636737133554, 0.16958010263680806, 0.0, 0.16958010263680806, 0.13120507751234178, 0.2139862647345275, 0.1460683498427064, 0.0, 0.3391602052736161, 0.0, 0.3391602052736161, 0.0, 0.0, 0.0, 0.0, 0.0, 0.13120507751234178, 0.0, 0.3391602052736161, 0.3391602052736161, 0.2139862647345275, 0.0, 0.38356636737133554, 0.0, 0.0, 0.0, 0.0, 0.0, 0.5087403079104241, 0.0, 0.1460683498427064, 0.2139862647345275, 0.3391602052736161, 0.3391602052736161, 0.13120507751234178, 0.0, 0.2139862647345275, 0.0, 0.2139862647345275, 0.0, 0.0, 0.1460683498427064, 0.0, 0.0, 0.13120507751234178, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0, 0.2139862647345275, 0.0, 0.1

  0%|          | 0/100 [00:00<?, ?it/s]

epoch 0:  training loss:  0.6616579


  1%|          | 1/100 [00:34<56:59, 34.54s/it]

[0.0, 0.2139862647345275, 0.0, 0.1460683498427064, 0.0, 0.1460683498427064, 0.0, 0.0, 0.16958010263680806, 0.2772734273550482, 0.0, 0.0, 0.30078518014914984, 0.0, 0.3391602052736161, 0.0, 0.0, 0.0, 0.0, 0.69921481985085, 0.0, 0.16958010263680806, 0.13120507751234178, 0.2139862647345275, 0.0, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0, 0.6164336326286642, 0.2139862647345275, 0.2139862647345275, 0.16958010263680806, 0.0, 0.16958010263680806, 0.0, 0.0, 0.2772734273550482, 0.0, 0.3391602052736161, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.3391602052736161, 0.34519134224686926, 0.0, 0.0, 0.7227265726449517, 0.529634717214042, 0.0, 0.0, 0.0, 0.0, 0.6548086577531306, 0.16958010263680806, 0.0, 0.2139862647345275, 0.8687949224876581, 0.1460683498427064, 0.0, 0.16958010263680806, 0.1460683498427064, 0.0, 0.1460683498427064, 0.0, 0.13120507751234178, 0.13120507751234178, 0.0, 0.0, 0.2772734273550482, 0.13120507751234178, 0.30078518014914984, 0.0, 0.0, 0.13120507751234178, 0.3391602052736161, 0.0, 0.1

...

epoch 97:  training loss:  0.41694415


 99%|█████████▉| 99/100 [27:27<00:14, 14.81s/it]

epoch 98:  training loss:  0.41682795


100%|██████████| 100/100 [27:42<00:00, 16.62s/it]

epoch 99:  training loss:  0.41625294


In [ ]:
ndcg = compute_ndcg(s.test_data,s.user_feature_matrix,s.item_feature_matrix, 5, model2)
print('init ndcg:', ndcg)
for epoch in tqdm.trange(100):
    model2.train()
    optimizer2.zero_grad()
    losses2 = []
    for user_behaviour_feature, item_aspect_feature, label in train_loader:
        user_behaviour_feature = user_behaviour_feature
        item_aspect_feature = item_aspect_feature
        label = label.float()
        out = model2(user_behaviour_feature, item_aspect_feature).squeeze()
        loss = loss_fn2(out, label)
        loss.backward()
        optimizer2.step()
        optimizer2.zero_grad()
        losses2.append(loss.detach().numpy())
        ave_train = np.mean(np.array(losses2))
    print('epoch %d: ' % epoch, 'training loss: ', ave_train)
    # compute necg
    if epoch % 10 == 0:
        ndcg = compute_ndcg(s.test_data, s.user_feature_matrix, s.item_feature_matrix, 5, model2)
        print('epoch %d: ' % epoch, 'training loss: ', ave_train, 'NDCG: ', ndcg)

[0.0, 0.1460683498427064, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.38356636737133554, 0.3391602052736161, 0.16958010263680806, 0.0, 0.1460683498427064, 0.2139862647345275, 0.3391602052736161, 0.0, 0.13120507751234178, 0.1460683498427064, 0.0, 0.16958010263680806, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.3391602052736161, 0.0, 0.0, 0.0, 0.0, 0.0, 0.13120507751234178, 0.0, 0.1460683498427064, 0.3391602052736161, 0.0, 0.13120507751234178, 0.0, 0.2139862647345275, 0.0, 0.38356636737133554, 0.0, 0.3391602052736161, 0.0, 0.0, 0.1460683498427064, 0.0, 0.0, 0.1460683498427064, 0.0, 0.0, 0.3391602052736161, 0.2139862647345275, 0.0, 0.0, 0.3391602052736161, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.2772734273550482, 0.2139862647345275, 0.0, 0.13120507751234178, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0,

  0%|          | 0/100 [00:00<?, ?it/s]

epoch 0:  training loss:  0.68585503


  1%|          | 1/100 [00:33<54:32, 33.05s/it]

[0.0, 0.1460683498427064, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.38356636737133554, 0.3391602052736161, 0.1460683498427064, 0.0, 0.0, 0.30078518014914984, 0.3391602052736161, 0.0, 0.0, 0.1460683498427064, 0.0, 0.2139862647345275, 0.0, 0.2139862647345275, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0, 0.0, 0.0, 0.0, 0.13120507751234178, 0.0, 0.1460683498427064, 0.3391602052736161, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.36005461457723387, 0.0, 0.16958010263680806, 0.0, 0.0, 0.1460683498427064, 0.0, 0.0, 0.1460683498427064, 0.0, 0.0, 0.2139862647345275, 0.2139862647345275, 0.0, 0.0, 0.3391602052736161, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.2772734273550482, 0.2139862647345275, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.16958010263680806, 0.0, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0, 0.0, 0.0, 0.0, 0.2139862647345275, 0.0, 0.0, 0.0, 0.213986264734

...

epoch 17:  training loss:  0.68568504


 19%|█▉        | 19/100 [05:24<20:58, 15.53s/it]

epoch 18:  training loss:  0.68580794


 19%|█▉        | 19/100 [05:34<23:46, 17.62s/it]


KeyboardInterrupt: ignored

In [ ]:
s.user_feature_matrix

array([[2.8484685, 4.980219 , 4.85611  , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 4.85611  , 2.8484685, ..., 0.       , 0.       ,
        0.       ],
       [0.       , 2.8484685, 2.8484685, ..., 0.       , 0.       ,
        0.       ],
       ...,
       [0.       , 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 0.       , 4.620593 , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 0.       , 2.8484685, ..., 0.       , 0.       ,
        0.       ]], dtype=float32)

In [ ]:
s.item_feature_matrix

array([[3.9242344, 3.9242344, 4.523188 , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ],
       ...,
       [0.       , 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ],
       [0.       , 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ]], dtype=float32)

In [ ]:
torch.save(model.state_dict(), "/content/drive/MyDrive/model_small.model")
base_model = BaseRecModel(s.num_features)
base_model.load_state_dict(torch.load("/content/drive/MyDrive/model_small.model"))
base_model.eval()
for param in base_model.parameters():
    param.requires_grad = False

In [ ]:
def evaluate_user_perspective(user_perspective_data, u_i_expl_dict):
    print(user_perspective_data)
    print(u_i_expl_dict)
    pres = []
    recs = []
    f1s = []
    for u_i, gt_features in user_perspective_data.items():
        if u_i in u_i_expl_dict:
            TP = 0
            pre_features = u_i_expl_dict[u_i]
            print('f: ', gt_features, pre_features)
            for feature in pre_features:
                if feature in gt_features:
                    TP += 1
            pre = TP / len(pre_features)
            rec = TP / len(gt_features)
            if (pre + rec) != 0:
                f1 = (2 * pre * rec) / (pre + rec)
            else:
                f1 = 0
            pres.append(pre)
            recs.append(rec)
            f1s.append(f1)
    ave_pre = np.mean(pres)
    ave_rec = np.mean(recs)
    ave_f1 = np.mean(f1s)
    return ave_pre, ave_rec, ave_f1

In [ ]:
def evaluate_model_perspective(
        rec_dict,
        u_i_exp_dict,
        base_model,
        user_feature_matrix,
        item_feature_matrix):
    """
    compute PN, PS and F_NS score for the explanations
    :param rec_dict: {u1: [i1, i2, i3, ...] , u2: [i1, i2, i3, ...]}
    :param u_i_exp_dict: {(u, i): [f1, f2, ...], ...}
    :param base_model: the trained base recommendation model
    :param user_feature_matrix: |u| x |p| matrix, the attention on each feature p for each user u
    :param item_feature_matrix: |i| x |p| matrix, the quality on each feature p for each item i
    :param rec_k: the length of the recommendation list, only generated explanations for the items on the list
    :param device: the device of the model
    :return: the mean of the PN, PS and FNS scores
    """
    pn_count = 0
    ps_count = 0
    for u_i, fs in u_i_exp_dict.items():
        user = u_i[0]
        target_item = u_i[1]
        features = set(fs)
        items = rec_dict[user]
        target_index = items.index(target_item)
        # compute PN
        cf_items_features = []
        for item in items:
            item_ori_feature = np.array(item_feature_matrix[item])
            item_cf_feature = np.array([0 if s in features else item_ori_feature[s]
                                        for s in range(len(item_ori_feature))], dtype='float32')
            cf_items_features.append(item_cf_feature)
        cf_ranking_scores = base_model(torch.from_numpy(np.array([user_feature_matrix[user]
                                                                      for i in range(len(cf_items_features))])
                                                            ),
                                           torch.from_numpy(np.array(cf_items_features))).squeeze()
        cf_score_list = cf_ranking_scores.detach().numpy()
        sorted_index = np.argsort(cf_score_list)[::-1]
        cf_rank = np.argwhere(sorted_index == target_index)[0, 0]  # the updated ranking of the current item
        if cf_rank > rec_k - 1:
            pn_count += 1
        # compute NS
        cf_items_features = []
        for item in items:
            item_ori_feature = np.array(item_feature_matrix[item])
            item_cf_feature = np.array([item_ori_feature[s] if s in features else 0
                                        for s in range(len(item_ori_feature))], dtype='float32')
            cf_items_features.append(item_cf_feature)
        cf_ranking_scores = base_model(torch.from_numpy(np.array([user_feature_matrix[user]
                                                                      for i in range(len(cf_items_features))])
                                                            ),
                                           torch.from_numpy(np.array(cf_items_features))).squeeze()
        cf_score_list = cf_ranking_scores.detach().numpy()
        sorted_index = np.argsort(cf_score_list)[::-1]
        cf_rank = np.argwhere(sorted_index == target_index)[0, 0]  # the updated ranking of the current item
        if cf_rank < rec_k:
            ps_count += 1
    if len(u_i_exp_dict) != 0:
        pn = pn_count / len(u_i_exp_dict)
        ps = ps_count / len(u_i_exp_dict)
        if (pn + ps) != 0:
            fns = (2 * pn * ps) / (pn + ps)
        else:
            fns = 0
    else:
        pn = 0
        ps = 0
        fns = 0
    return pn, ps, fns

In [ ]:
# class ExpOptimizationModel(torch.nn.Module):
#     def __init__(self, base_model, rec_dataset):
#         super(ExpOptimizationModel, self).__init__()
#         self.base_model = base_model
#         self.rec_dataset = rec_dataset
#         self.u_i_exp_dict = {}  # {(user, item): [f1, f2, f3 ...], ...}
#         self.user_feature_matrix = torch.from_numpy(self.rec_dataset.user_feature_matrix)
#         self.item_feature_matrix = torch.from_numpy(self.rec_dataset.item_feature_matrix)
#         self.rec_dict, self.user_perspective_test_data = self.generate_rec_dict()

#     def generate_rec_dict(self):
#         rec_dict = {}
#         correct_rec_dict = {}  # used for user-side evaluation
#         for row in self.rec_dataset.test_data:
#             user = row[0]
#             items = row[1]
#             labels = row[2]
#             correct_rec_dict[user] = []
#             user_features = self.user_feature_matrix[user].repeat(len(items), 1)
#             scores = self.base_model(user_features,
#                         self.item_feature_matrix[items]).squeeze()
#             scores = np.array(scores)
#             sort_index = sorted(range(len(scores)), key=lambda k: scores[k], reverse=True)
#             sorted_items = [items[i] for i in sort_index]
#             rec_dict[user] = sorted_items
#             for i in range(rec_k):  # find the correct items and add to the user side test data
#                 if labels[sort_index[i]] == 1:
#                     correct_rec_dict[user].append(items[sort_index[i]])
#         user_item_feature_dict = {}  # {(u, i): f, (u, i): f]
#         print(correct_rec_dict)

#         for row in self.rec_dataset.sentiment_data:
#             user = row[0]
#             item = row[1]
#             user_item_feature_dict[(user, item)] = []
#             for fos in row[2:]:
#                 feature = fos[0]
#                 user_item_feature_dict[(user, item)].append(feature)
#         user_perspective_test_data = {}  # {(u, i):f, (u, i): f]}
#         for user, items in correct_rec_dict.items():
#             for item in items:
#                 # print(item)
#                 # if (user, item)not in user_item_feature_dict:
#                 #   feature = 0
#                 #   print(":(")
#                 # else:
#                 feature = user_item_feature_dict[(user, item)]
#                 # print(feature)
#                 user_perspective_test_data[(user, item)] = feature
#         print(rec_dict)
#         print(len(user_perspective_test_data))
#         return rec_dict, user_perspective_test_data

#     def generate_explanation(self):
#         # u_i_exps_dict = {}  # {(user, item): [f1, f2, f3 ...], ...}
#         test_num = -1
#         exp_nums = []
#         exp_complexities = []
#         no_exp_count = 0
#         if test_num==-1:
#             test_num = len(list(self.rec_dict.items()))
#         else:
#             test_num = test_num
#         for user, items in tqdm.tqdm(list(self.rec_dict.items())[:test_num]):
#             items = self.rec_dict[user]
#             margin_item = items[rec_k]
#             margin_score = self.base_model(self.user_feature_matrix[user].unsqueeze(0),
#                             self.item_feature_matrix[margin_item].unsqueeze(0)).squeeze()
#             if user_mask:
#                 # mask_vec = self.generate_mask(user)
#                 mask_vec = torch.where(self.user_feature_matrix[user]>0, 1., 0.).unsqueeze(0)  # only choose exps from the user cared aspects
#             else:
#                 mask_vec = torch.ones(self.rec_dataset.num_features).unsqueeze(0)
#             for item in items[: rec_k]:
#                 explanation_features, exp_num, exp_complexity = self.explain(
#                     self.user_feature_matrix[user],
#                     self.item_feature_matrix[item],
#                     margin_score,
#                     mask_vec)
#                 if explanation_features is None:
#                     # print('no explanation for user %d and item %d' % (user, item))
#                     no_exp_count += 1
#                 else:
#                     self.u_i_exp_dict[(user, item)] = explanation_features
#                     exp_nums.append(exp_num)
#                     exp_complexities.append(exp_complexity)
#         print('ave num: ', np.mean(exp_nums), 'ave complexity: ', np.mean(exp_complexities),"No Exp : ",no_exp_count)
#         return True

#     def explain(self, user_feature, item_feature, margin_score, mask_vec):
#         exp_generator = EXPGenerator(
#             self.rec_dataset,
#             self.base_model,
#             user_feature,
#             item_feature,
#             margin_score,
#             mask_vec)

#         # optimization
#         optimizer = torch.optim.SGD(exp_generator.parameters(), lr=lr, weight_decay=0)
#         exp_generator.train()
#         lowest_loss = None
#         lowest_bpr = None
#         lowest_l2 = 0
#         optimize_delta = None
#         score = exp_generator()
#         bpr, l2, l1, loss = exp_generator.loss(score)
#         # print('init: ', 0, '  train loss: ', loss, '  bpr: ', bpr, '  l2: ', l2, '  l1: ', l1)
#         lowest_loss = loss
#         optimize_delta = exp_generator.delta.detach().numpy()
#         lowest_l2 = l2
#         for epoch in range(step):
#             exp_generator.zero_grad()
#             score = exp_generator()
#             bpr, l2, l1, loss = exp_generator.loss(score)
#             loss.backward()
#             optimizer.step()
#             if loss < lowest_loss:
#                 lowest_loss = loss
#                 lowest_l2 = l2
#                 lowest_bpr = bpr
#                 optimize_delta = exp_generator.delta.detach().numpy()
#         if lowest_bpr >= lam * alp:
#             explanation_features = None
#             exp_num = None
#             exp_complexity = None
#         else:
#             # optimize_delta = exp_generator.delta.detach().to('cpu').numpy()
#             explanation_features = np.argwhere(optimize_delta < - mask_thresh).squeeze(axis=1)
#             if len(explanation_features) == 0:
#                 explanation_features = np.array([np.argmin(optimize_delta)])
#             exp_num = len(explanation_features)
#             exp_complexity = lowest_l2.detach().numpy() + gam * exp_num
#         return explanation_features, exp_num, exp_complexity

#     def user_side_evaluation(self):
#         ave_pre, ave_rec, ave_f1 = evaluate_user_perspective(self.user_perspective_test_data, self.u_i_exp_dict)
#         print('user\'s perspective:')
#         print('ave pre: ', ave_pre, '  ave rec: ', ave_rec, '  ave f1: ', ave_f1)



# class EXPGenerator(torch.nn.Module):
#     def __init__(self, rec_dataset, base_model, user_feature, item_feature, margin_score, mask_vec):
#         super(EXPGenerator, self).__init__()
#         self.rec_dataset = rec_dataset
#         self.base_model = base_model
#         self.user_feature = user_feature
#         self.item_feature = item_feature
#         self.margin_score = margin_score
#         self.mask_vec = mask_vec
#         self.feature_range = [0, 5]  # hard coded, should be improved later
#         self.delta_range = self.feature_range[1] - self.feature_range[0]  # the maximum feature value.
#         self.delta = torch.nn.Parameter(
#             torch.FloatTensor(len(self.user_feature)).uniform_(-self.delta_range, 0))

#     def get_masked_item_feature(self):
#         item_feature_star = torch.clamp(
#             (self.item_feature + torch.clamp((self.delta * self.mask_vec), -self.delta_range, 0)),
#             self.feature_range[0], self.feature_range[1])
#         return item_feature_star

#     def forward(self):
#         item_feature_star = self.get_masked_item_feature()
#         score = self.base_model(self.user_feature.unsqueeze(0), item_feature_star)
#         return score

#     def loss(self, score):
#         bpr = torch.nn.functional.relu(alp + score - self.margin_score) * lam
#         l2 = torch.linalg.norm(self.delta)
#         l1 = torch.linalg.norm(self.delta, ord=1) * gam
#         loss = l2 + bpr + l1
#         return bpr, l2, l1, loss

In [ ]:
# opt_model = ExpOptimizationModel(base_model=base_model,rec_dataset=s)
# # opt_model.generate_rec_dict()
# opt_model.generate_explanation()
# opt_model.user_side_evaluation()
# opt_model.model_side_evaluation()

{0: [], 1: [3995], 2: [], 3: [1572], 4: [], 5: [], 6: [4127], 7: [], 8: [], 9: [], 10: [9161, 9242], 11: [], 12: [2585, 131], 13: [], 14: [], 15: [], 16: [], 17: [190], 18: [], 19: [9303, 9140, 9163, 9279], 20: [], 21: [4127, 1272], 22: [8802], 23: [5312], 24: [], 25: [], 26: [], 27: [], 28: [3451], 29: [], 30: [], 31: [8215], 32: [5086, 8320], 33: [1879], 34: [1879, 4088], 35: [1604], 36: [5638], 37: [6043, 5638, 6042], 38: [3595], 39: [], 40: [7204, 4614], 41: [], 42: [], 43: [], 44: [], 45: [], 46: [], 47: [2034], 48: [5312, 2138], 49: [3150], 50: [8470], 51: [3857, 4160], 52: [], 53: [], 54: [9134, 9137, 8919, 9135], 55: [], 56: [], 57: [], 58: [], 59: [9248, 9106], 60: [], 61: [], 62: [], 63: [8213, 8814, 8210, 8212], 64: [], 65: [], 66: [8815, 7805], 67: [], 68: [], 69: [], 70: [], 71: [9138], 72: [7657, 4589], 73: [], 74: [], 75: [], 76: [9315], 77: [9163, 9136, 9127, 8706], 78: [9081], 79: [], 80: [6195], 81: [], 82: [9074], 83: [], 84: [], 85: [9166], 86: [], 87: [], 88: [5601

100%|██████████| 2659/2659 [6:04:23<00:00,  8.22s/it]


ave num:  8.455711206896552 ave complexity:  15.60032349682397 No Exp :  4015
{(1, 3995): [1, 62], (3, 1572): [156], (6, 4127): [39, 39, 123], (10, 9161): [2, 2, 4, 69, 405], (10, 9242): [2, 2, 1, 69], (12, 2585): [63], (12, 131): [74], (17, 190): [5, 5], (19, 9303): [12, 73, 272, 3, 66, 2, 2, 2, 2, 7, 143, 69, 5], (19, 9140): [2, 2, 63, 5], (19, 9163): [13, 273, 273], (19, 9279): [2, 18, 18, 138, 138, 138], (21, 4127): [222], (21, 1272): [32, 186, 60], (22, 8802): [71, 1, 26], (23, 5312): [415, 115, 2, 357, 357, 2, 357, 357, 357], (28, 3451): [3, 139, 139, 65], (31, 8215): [49, 13, 13, 13, 13, 7, 13, 7], (32, 5086): [65, 462], (32, 8320): [273, 273], (33, 1879): [76, 18, 44], (34, 1879): [6, 2, 11, 6], (34, 4088): [62, 62], (35, 1604): [6, 6, 127], (36, 5638): [2, 78, 56, 123, 2, 93], (37, 6043): [29, 22, 22, 413, 1, 1, 1, 44, 140, 140, 53, 22, 208], (37, 5638): [15, 93], (37, 6042): [22, 1, 1, 1, 59, 27, 140, 140, 140, 53, 208], (38, 3595): [243, 163], (40, 7204): [32, 127, 123], (40

TypeError: ignored

In [ ]:
with open('/content/drive/MyDrive/OPTmodel_small.pickle', 'wb') as outp:
    pickle.dump(opt_model, outp, pickle.HIGHEST_PROTOCOL)


In [ ]:
class EOptimizer(torch.nn.Module):
  def __init__(self,Recommender,dataset):
    super(EOptimizer,self).__init__()
    self.Recommender = Recommender
    self.dataset=dataset
    self.u_f_matrix = torch.from_numpy(self.dataset.user_feature_matrix)
    self.i_f_matrix = torch.from_numpy(self.dataset.item_feature_matrix)
    self.rec_dict={}
    self.true_record_dict = {}
    self.u_i_exp_dict={}
    self.e_rec_dict()
  def e_rec_dict(self):
    rec_dict={}
    true_record = {}
    for row in self.dataset.test_data:
      u = row[0]
      items = row[1]
      label = row[2]
      true_record[u]=[]
      #Score for each u-item ranking
      scores = np.array(self.Recommender(self.u_f_matrix[u].repeat(len(items),1),self.i_f_matrix[items]).squeeze())
      # # Sort items based on scores in descending order
      # sorted_items = sorted(items, key=lambda item: score[items.index(item)], reverse=True)
      sort_index = sorted(range(len(scores)), key=lambda k: scores[k], reverse=True)
      sorted_items = [items[i] for i in sort_index]
      # Add the sorted items to the user's recommendation dictionary
      rec_dict[u] = sorted_items
      # Find the top recommended items that are also correct (i.e., have a label of 1) and add them to the correct recommendation dictionary
      for i in range(rec_k):
          if label[sort_index[i]] == 1:
              true_record[u].append(items[sort_index[i]])
          # if i == rec_k-1:
          #     break

    user_feature_item_dict={}
    true_record_dict={}
    print(true_record)
    for row in self.dataset.sentiment_data:
      u = row[0]
      item = row[1]
      user_feature_item_dict[(u,item)]=[]
      for fos in row[2:]:
        feature = fos[0]
        user_feature_item_dict[(u,item)].append(feature)
    for u, items in true_record.items():
      for i in items:
        print(item)
        if (u, item)not in user_feature_item_dict:
          feature = 0
          print(":(")
        else:
          feature = user_feature_item_dict[(u, item)]
          print(feature)
        # features = user_feature_item_dict[(u,item)]
        true_record_dict[(u,item)] = feature
    self.rec_dict=rec_dict
    self.true_record_dict = true_record_dict
    print(rec_dict)
    print(len(true_record_dict))
  def generate_explanation(self):
    test_num = 10 #len()
    no_exp=0
    nums=[]
    e_complexity = []
    for u, items in tqdm.tqdm(list(self.rec_dict.items())[:test_num]):
      items = self.rec_dict[u]
      k_plus_1_item = items[rec_k]
      k_plus_1_score = self.Recommender(self.u_f_matrix[u].unsqueeze(0),self.i_f_matrix[k_plus_1_item].unsqueeze(0)).squeeze()
      masking = torch.ones(self.dataset.num_features).unsqueeze(0)
      for i in items[:rec_k]:
        e_features, num,complexity = self.explain(self.u_f_matrix[u],self.i_f_matrix[i],k_plus_1_score,masking)
        if e_features is None:
          no_exp +=1
        else:
          self.u_i_exp_dict[(u,i)] = e_features
          nums.append(num)
          e_complexity.append(complexity)
    print("Avergae Number of exp :", np.mean(nums), "Average Complexity :",np.mean(e_complexity),"No Explanations :",no_exp)
    return True
  def explain(self, u_f,i_f,k_plus_1_score,mask):
    generator = Generator(self.dataset,self.Recommender,u_f,i_f,k_plus_1_score,mask)
    optimizer = torch.optim.SGD(generator.parameters(),lr,weight_decay =0)
    generator.train()
    score = generator()
    bpr,l2,l1,loss = generator.loss(score)
    least_loss=loss
    least_l2=l2
    least_bpr = bpr
    opt_delta = generator.delta.detach().numpy()
    for epoch in range(step):
      generator.zero_grad()
      score = generator()
      bpr,l2,l1,loss = generator.loss(score)
      loss.backward()
      optimizer.step()
      if loss<least_loss:
        least_loss = loss
        least_l2=l2
        least_bpr = bpr
        opt_delta = generator.delta.detach().numpy()
    if least_bpr >= Lambda*Alpha:
      features = None
      num= None
      complexity = None
    else :
      features = np.argwhere(opt_delta < - threshold).squeeze(axis=1)
      if(len(features)==0):
        features = np.array([np.argmin(opt_delta)])
      num = len(features)
      complexity=least_l2.detach().numpy() + gamma*num
    return features, num,complexity

  def user_side_evaluation(self):
    ave_pre, ave_rec, ave_f1 = evaluate_user_perspective(self.true_record_dict, self.u_i_exp_dict)
    print('user\'s perspective:')
    print('ave pre: ', ave_pre, '  ave rec: ', ave_rec, '  ave f1: ', ave_f1)

  def model_side_evaluation(self):
        ave_pn, ave_ps, ave_fns = evaluate_model_perspective(
            self.rec_dict,
            self.u_i_exp_dict,
            self.Recommender,
            self.dataset.user_feature_matrix,
            self.dataset.item_feature_matrix)
        print('model\'s perspective:')
        print('ave PN: ', ave_pn, '  ave PS: ', ave_ps, '  ave F_{NS}: ', ave_fns)






In [ ]:
class Generator(torch.nn.Module):
  def __init__(self,dataset,Recommender,user_feature,item_feature,k_plus_1_score,masking):
    super(Generator,self).__init__()
    self.dataset= dataset
    self.Recommender = Recommender
    self.user_feature = user_feature
    self.i_f= item_feature
    self.k_plus_1_score = k_plus_1_score
    self.masking = masking
    self.feature_range = [range_i,range_j]
    self.delta_range = self.feature_range[1] - self.feature_range[0]
    self.delta = torch.nn.Parameter(torch.FloatTensor(len(self.user_feature)).uniform_(-self.delta_range,0))
  def get_masked_i_f(self):
    i_f = torch.clamp( self.i_f + torch.clamp((self.delta * self.masking),-self.delta_range,0),self.feature_range[0],self.feature_range[1])
    return i_f
  def forward(self):
    i_f = self.get_masked_i_f()
    score = self.Recommender(self.user_feature.unsqueeze(0),i_f)
    return score
  def loss(self,score):
    bpr = torch.nn.functional.relu(Alpha + score -self.k_plus_1_score)*Lambda
    l2 = torch.linalg.norm(self.delta)
    l1 = torch.linalg.norm(self.delta,ord=1)*gamma
    loss = l2+l1+bpr
    return bpr,l2,l1,loss

In [ ]:
# optimize_exp = EOptimizer(base_model,s)
optimize_exp.generate_explanation()
optimize_exp.user_side_evaluation()
optimize_exp.model_side_evaluation()

Streaming output truncated to the last 5000 lines.
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422
:(
9422


100%|██████████| 10/10 [00:58<00:00,  5.84s/it]
/usr/local/lib/python3.9/dist-packages/numpy/core/fromnumeric.py:3474: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.9/dist-packages/numpy/core/_methods.py:189: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


Avergae Number of exp : 8.023255813953488 Average Complexity : 14.803181409835815 No Explanations : 7
{(1, 9422): 0, (2, 9422): 0, (6, 9422): 0, (9, 9422): 0, (11, 9422): 0, (12, 9422): 0, (14, 9422): 0, (16, 9422): 0, (19, 9422): 0, (21, 9422): 0, (22, 9422): 0, (23, 9422): 0, (27, 9422): 0, (28, 9422): 0, (29, 9422): 0, (31, 9422): 0, (32, 9422): 0, (33, 9422): 0, (35, 9422): 0, (36, 9422): 0, (37, 9422): 0, (39, 9422): 0, (40, 9422): 0, (41, 9422): 0, (46, 9422): 0, (47, 9422): 0, (48, 9422): 0, (49, 9422): 0, (50, 9422): 0, (51, 9422): 0, (53, 9422): 0, (54, 9422): 0, (59, 9422): 0, (61, 9422): 0, (63, 9422): 0, (66, 9422): 0, (71, 9422): 0, (75, 9422): 0, (76, 9422): 0, (77, 9422): 0, (80, 9422): 0, (81, 9422): 0, (82, 9422): 0, (84, 9422): 0, (88, 9422): 0, (92, 9422): 0, (93, 9422): 0, (96, 9422): 0, (97, 9422): 0, (101, 9422): 0, (102, 9422): 0, (103, 9422): 0, (106, 9422): 0, (107, 9422): 0, (109, 9422): 0, (110, 9422): 0, (111, 9422): 0, (112, 9422): 0, (115, 9422): 0, (117, 

In [ ]:
# import pandas as pd
# with open('/content/drive/MyDrive/OPTmodel_small.pickle', "rb") as f:
#     object = pickle.load(f)

# df = pd.DataFrame(object)
# df.to_csv(r'file2.csv')
# print(df.head())

ValueError: ignored

In [ ]:
print(object)
print(type(object))

ExpOptimizationModel(
  (base_model): BaseRecModel(
    (fc): Sequential(
      (0): Linear(in_features=1162, out_features=1024, bias=True)
      (1): ReLU()
      (2): Linear(in_features=1024, out_features=256, bias=True)
      (3): ReLU()
      (4): Linear(in_features=256, out_features=1, bias=True)
      (5): Sigmoid()
    )
  )
)
<class '__main__.ExpOptimizationModel'>
